# Seq2seq model - pitch-based
- [_Joplin_](http://kern.humdrum.org/search?s=t&keyword=Joplin) dataset is used as the training data for this model.
- A song is parsed into a sequence (containing one or multiple measures) of chords. 
    - Chords are represented in sequence of pitches, separated by '/', thus this model is called pitch-based; i.e., chords are represented as a sequence of one hot vectors that representing different pitches. 
    - In [chord-based model](Seq2seq model - Joplin.ipynb), each chord is represented as a single multi-hot vector.

In [1]:
import os
import util

## Part 1 - chord sequence to chord sequence
### Load data
- _Chorales_ dataset is used. 
- The data is parsed from kern score using <code>rchoraledata</code> tool in [_Humdrum Extras_](http://wiki.ccarh.org/wiki/Humdrum_Extras). See the [embedding notebook](Chord_Embeddings - Joplin.ipynb) for details.
- Filtering data
    - Only songs in 4/4 time signature are selected since most of the songs in this dataset are in 4/4.

In [2]:
music_type = 'chorales'
dataset = 'datasets/' + music_type

In [3]:
files = [f for f in os.listdir(dataset+'/dat/') if f.endswith('.dat')]
files = files.sort()

In [4]:
files = [f for f in os.listdir(dataset+'/krn/') if f.endswith('.krn')]
filtered_files = [] # only use song with time sig 2/4

for file in files[:]:
    basename = file[:-4]
    #! transpose -k c $dataset/krn/$basename\.krn | rchoraledata > $dataset/dat/$basename\.dat
    ret = ! beat -Ca $dataset/krn/$basename\.krn | beat -Ua  | extractx -s '$1-$'  | ridx -H | sortcount -p
    if ret[0] == '100\t4\t4': filtered_files.append(file)

In [5]:
filtered_files.sort()
filtered_files = [f[:-4] + '.dat' for f in filtered_files]

### Build dictionaries for pitch and time information
- Indexing different pitches and time durations.

In [6]:
# c_data: [song, measure, chord, pitch]
# t_data: [song, measure, dur]
t_data, c_data, t_val2idx, t_idx2val, c_val2idx, c_idx2val = (util.parse_dat_dir(dataset, filtered_files))

#### Add start, delimeter, and end tokens to the dictionaries
- <code>S</code> -  the start of a sequence
- <code>END</code> - the end of a sequence
- <code>/</code> - a delimeter that separates different chords

In [7]:
c_val2idx['<S>'] = len(c_val2idx)
c_idx2val[c_val2idx['<S>']] = '<S>'
c_val2idx['/'] = len(c_val2idx)
c_idx2val[c_val2idx['/']] = '/'
c_val2idx['<END>'] = len(c_val2idx)
c_idx2val[c_val2idx['<END>']] = '<END>'

t_val2idx['<S>'] = len(t_val2idx)
t_idx2val[t_val2idx['<S>']] = '<S>'
t_val2idx['<END>'] = len(t_val2idx)
t_idx2val[t_val2idx['<END>']] = '<END>'

In [8]:
meas_per_seq = 2
encoder_input_data, decoder_input_data, decoder_target_data = util.gen_data_rec_pitch_based(c_data, c_val2idx, meas_per_seq=meas_per_seq) #[song, measure, chord]

### Generate input and target data that fits the model requirements
- The data is in the form of a list of 3D arrays.
    - Each entry in the list represents a song.
    - The 3 dimensions are for <code>[num_seq, max_seq_len, num_features]</code>.
    - Padded with zeros if <code>max_seq_len</code> is not met.

In [9]:
encoder_input_data = util.get_data_fitted(encoder_input_data)
decoder_input_data = util.get_data_fitted(decoder_input_data)
decoder_target_data = util.get_data_fitted(decoder_target_data)

### Build the seq2seq model - predict next chords sequence from current chords sequence
- Referenced from a [Keras seq2seq tutorial](https://blog.keras.io/a-ten-minute-introduction-to-sequence-to-sequence-learning-in-keras.html).
- Have a look at [Keras](https://keras.io), which is a easy-to-use neural network API.

In [10]:
from __future__ import print_function

from keras.models import Model
from keras.layers import Input, LSTM, Dense
import numpy as np

batch_size = 64  # Batch size for training.
iterations = 40  # Number of epochs to train for.
latent_dim = 256 

/anaconda3/lib/python3.6/site-packages/h5py/__init__.py:36: FutureWarning: Conversion of the second argument of issubdtype from `float` to `np.floating` is deprecated. In future, it will be treated as `np.float64 == np.dtype(float).type`.
  from ._conv import register_converters as _register_converters
Using TensorFlow backend.


In [11]:
num_encoder_tokens = len(c_val2idx)
num_decoder_tokens = num_encoder_tokens
max_encoder_seq_length = None # different max-seq-len for different songs
max_decoder_seq_length = None

In [12]:
# Define an input sequence and process it.
encoder_inputs = Input(shape=(None, num_encoder_tokens))
encoder = LSTM(latent_dim, return_state=True)
encoder_outputs, state_h, state_c = encoder(encoder_inputs)
# We discard `encoder_outputs` and only keep the states.
encoder_states = [state_h, state_c]

In [13]:
# Set up the decoder, using `encoder_states` as initial state.
decoder_inputs = Input(shape=(None, num_decoder_tokens))
# We set up our decoder to return full output sequences,
# and to return internal states as well. We don't use the
# return states in the training model, but we will use them in inference.
decoder_lstm = LSTM(latent_dim, return_sequences=True, return_state=True)
decoder_outputs, _, _ = decoder_lstm(decoder_inputs,
                                     initial_state=encoder_states)
decoder_dense = Dense(num_decoder_tokens, activation='softmax')
decoder_outputs = decoder_dense(decoder_outputs)

In [14]:
#model.reset_states()
model = Model([encoder_inputs, decoder_inputs], decoder_outputs)

In [15]:
model.compile(optimizer='rmsprop', loss='categorical_crossentropy')

In [16]:
model.summary()

__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_1 (InputLayer)            (None, None, 110)    0                                            
__________________________________________________________________________________________________
input_2 (InputLayer)            (None, None, 110)    0                                            
__________________________________________________________________________________________________
lstm_1 (LSTM)                   [(None, 256), (None, 375808      input_1[0][0]                    
__________________________________________________________________________________________________
lstm_2 (LSTM)                   [(None, None, 256),  375808      input_2[0][0]                    
                                                                 lstm_1[0][1]                     
          

### Start training

In [17]:
batch_size = 64  # Batch size for training.
iterations = 60  # Number of epochs to train for.
latent_dim = 256  # Latent dimensionality of the encoding space.

for it in range(iterations):
    print('='*50)
    print('Iteration {}/{}'.format(it + 1, iterations))
    for i in range(len(c_data)):
        model.fit([encoder_input_data[i], decoder_input_data[i]], decoder_target_data[i],
              batch_size=None,
              epochs=1,
              validation_split=0.01)

Iteration 1/60
Train on 10 samples, validate on 1 samples
Epoch 1/1
10/10 [==============================] - 6s 571ms/step - loss: 3.4424 - val_loss: 2.7419
Train on 7 samples, validate on 1 samples
Epoch 1/1
7/7 [==============================] - 1s 103ms/step - loss: 4.2000 - val_loss: 3.3471
Train on 7 samples, validate on 1 samples
Epoch 1/1
7/7 [==============================] - 1s 78ms/step - loss: 3.8420 - val_loss: 2.6844
Train on 14 samples, validate on 1 samples
Epoch 1/1
14/14 [==============================] - 1s 67ms/step - loss: 4.0163 - val_loss: 3.3433
Train on 5 samples, validate on 1 samples
Epoch 1/1
5/5 [==============================] - 1s 131ms/step - loss: 3.5283 - val_loss: 1.9831
Train on 17 samples, validate on 1 samples
Epoch 1/1
17/17 [==============================] - 1s 44ms/step - loss: 3.2634 - val_loss: 2.6583
Train on 9 samples, validate on 1 samples
Epoch 1/1
9/9 [==============================] - 1s 78ms/step - loss: 3.6821 - val_loss: 3.3413
Train o

Train on 11 samples, validate on 1 samples
Epoch 1/1
11/11 [==============================] - 1s 56ms/step - loss: 3.3966 - val_loss: 3.1192
Train on 10 samples, validate on 1 samples
Epoch 1/1
10/10 [==============================] - 0s 42ms/step - loss: 3.0869 - val_loss: 2.9350
Train on 6 samples, validate on 1 samples
Epoch 1/1
6/6 [==============================] - 1s 89ms/step - loss: 3.3913 - val_loss: 3.4231
Train on 21 samples, validate on 1 samples
Epoch 1/1
21/21 [==============================] - 1s 30ms/step - loss: 2.7937 - val_loss: 2.8870
Train on 17 samples, validate on 1 samples
Epoch 1/1
17/17 [==============================] - 1s 37ms/step - loss: 2.8002 - val_loss: 1.7926
Train on 10 samples, validate on 1 samples
Epoch 1/1
10/10 [==============================] - 1s 74ms/step - loss: 3.3800 - val_loss: 2.2677
Train on 5 samples, validate on 1 samples
Epoch 1/1
5/5 [==============================] - 0s 86ms/step - loss: 3.7350 - val_loss: 3.4508
Train on 8 samples,

Train on 7 samples, validate on 1 samples
Epoch 1/1
7/7 [==============================] - 0s 71ms/step - loss: 2.1257 - val_loss: 1.4869
Train on 37 samples, validate on 1 samples
Epoch 1/1
37/37 [==============================] - 2s 46ms/step - loss: 2.0187 - val_loss: 2.3886
Train on 29 samples, validate on 1 samples
Epoch 1/1
29/29 [==============================] - 1s 34ms/step - loss: 2.6197 - val_loss: 2.6479
Train on 11 samples, validate on 1 samples
Epoch 1/1
11/11 [==============================] - 0s 44ms/step - loss: 2.4114 - val_loss: 2.0753
Train on 13 samples, validate on 1 samples
Epoch 1/1
13/13 [==============================] - 1s 39ms/step - loss: 2.8627 - val_loss: 2.3275
Train on 5 samples, validate on 1 samples
Epoch 1/1
5/5 [==============================] - 1s 116ms/step - loss: 3.0541 - val_loss: 2.4603
Train on 18 samples, validate on 1 samples
Epoch 1/1
18/18 [==============================] - 1s 50ms/step - loss: 2.5311 - val_loss: 2.2203
Train on 10 sample

Train on 24 samples, validate on 1 samples
Epoch 1/1
24/24 [==============================] - 1s 45ms/step - loss: 2.0094 - val_loss: 3.2020
Train on 6 samples, validate on 1 samples
Epoch 1/1
6/6 [==============================] - 0s 44ms/step - loss: 2.0065 - val_loss: 2.7216
Train on 45 samples, validate on 1 samples
Epoch 1/1
45/45 [==============================] - 2s 48ms/step - loss: 2.8542 - val_loss: 2.0199
Train on 12 samples, validate on 1 samples
Epoch 1/1
12/12 [==============================] - 1s 61ms/step - loss: 2.5469 - val_loss: 2.4193
Train on 12 samples, validate on 1 samples
Epoch 1/1
12/12 [==============================] - 1s 65ms/step - loss: 2.3625 - val_loss: 1.7399
Train on 13 samples, validate on 1 samples
Epoch 1/1
13/13 [==============================] - 1s 44ms/step - loss: 2.3321 - val_loss: 2.8166
Train on 11 samples, validate on 1 samples
Epoch 1/1
11/11 [==============================] - 1s 62ms/step - loss: 2.3892 - val_loss: 1.9221
Train on 8 sampl

Train on 13 samples, validate on 1 samples
Epoch 1/1
13/13 [==============================] - 1s 42ms/step - loss: 2.2681 - val_loss: 1.9827
Train on 9 samples, validate on 1 samples
Epoch 1/1
9/9 [==============================] - 1s 84ms/step - loss: 2.3726 - val_loss: 2.3297
Train on 10 samples, validate on 1 samples
Epoch 1/1
10/10 [==============================] - 1s 57ms/step - loss: 2.2156 - val_loss: 2.0965
Train on 9 samples, validate on 1 samples
Epoch 1/1
9/9 [==============================] - 0s 55ms/step - loss: 2.2701 - val_loss: 2.2558
Train on 7 samples, validate on 1 samples
Epoch 1/1
7/7 [==============================] - 1s 97ms/step - loss: 2.5584 - val_loss: 1.6624
Train on 16 samples, validate on 1 samples
Epoch 1/1
16/16 [==============================] - 1s 52ms/step - loss: 2.4983 - val_loss: 1.9476
Train on 11 samples, validate on 1 samples
Epoch 1/1
11/11 [==============================] - 1s 53ms/step - loss: 2.0890 - val_loss: 2.3495
Train on 7 samples, va

...

Train on 9 samples, validate on 1 samples
Epoch 1/1
9/9 [==============================] - 0s 40ms/step - loss: 0.1380 - val_loss: 0.4716
Train on 13 samples, validate on 1 samples
Epoch 1/1
13/13 [==============================] - 0s 21ms/step - loss: 0.2767 - val_loss: 1.0604
Train on 6 samples, validate on 1 samples
Epoch 1/1
6/6 [==============================] - 0s 27ms/step - loss: 0.0816 - val_loss: 0.9569
Train on 9 samples, validate on 1 samples
Epoch 1/1
9/9 [==============================] - 0s 22ms/step - loss: 0.0860 - val_loss: 1.0079
Train on 10 samples, validate on 1 samples
Epoch 1/1
10/10 [==============================] - 0s 28ms/step - loss: 0.0681 - val_loss: 0.8179
Train on 7 samples, validate on 1 samples
Epoch 1/1
7/7 [==============================] - 0s 58ms/step - loss: 0.0779 - val_loss: 0.6685
Train on 11 samples, validate on 1 samples
Epoch 1/1
11/11 [==============================] - 1s 60ms/step - loss: 0.1022 - val_loss: 0.5641
Train on 10 samples, vali

Train on 7 samples, validate on 1 samples
Epoch 1/1
7/7 [==============================] - 0s 37ms/step - loss: 0.0752 - val_loss: 0.9290
Train on 10 samples, validate on 1 samples
Epoch 1/1
10/10 [==============================] - 0s 39ms/step - loss: 0.0546 - val_loss: 0.3257
Train on 6 samples, validate on 1 samples
Epoch 1/1
6/6 [==============================] - 0s 42ms/step - loss: 0.1160 - val_loss: 1.3129
Train on 9 samples, validate on 1 samples
Epoch 1/1
9/9 [==============================] - 0s 27ms/step - loss: 0.1673 - val_loss: 1.3566
Train on 9 samples, validate on 1 samples
Epoch 1/1
9/9 [==============================] - 0s 23ms/step - loss: 0.1530 - val_loss: 0.8549
Train on 7 samples, validate on 1 samples
Epoch 1/1
7/7 [==============================] - 0s 19ms/step - loss: 0.0589 - val_loss: 0.3906
Train on 7 samples, validate on 1 samples
Epoch 1/1
7/7 [==============================] - 1s 76ms/step - loss: 0.0425 - val_loss: 0.1531
Train on 37 samples, validate o

Train on 11 samples, validate on 1 samples
Epoch 1/1
11/11 [==============================] - 0s 26ms/step - loss: 0.0378 - val_loss: 0.3684
Train on 9 samples, validate on 1 samples
Epoch 1/1
9/9 [==============================] - 0s 33ms/step - loss: 0.2075 - val_loss: 1.4746
Train on 27 samples, validate on 1 samples
Epoch 1/1
27/27 [==============================] - 1s 25ms/step - loss: 0.6577 - val_loss: 1.7389
Train on 14 samples, validate on 1 samples
Epoch 1/1
14/14 [==============================] - 0s 34ms/step - loss: 0.1106 - val_loss: 0.8054
Train on 12 samples, validate on 1 samples
Epoch 1/1
12/12 [==============================] - 0s 25ms/step - loss: 0.1985 - val_loss: 0.8615
Train on 15 samples, validate on 1 samples
Epoch 1/1
15/15 [==============================] - 1s 39ms/step - loss: 0.1255 - val_loss: 0.6400
Train on 24 samples, validate on 1 samples
Epoch 1/1
24/24 [==============================] - 0s 20ms/step - loss: 0.3814 - val_loss: 1.6130
Train on 6 sampl

Train on 8 samples, validate on 1 samples
Epoch 1/1
8/8 [==============================] - 0s 53ms/step - loss: 0.1195 - val_loss: 0.4633
Train on 9 samples, validate on 1 samples
Epoch 1/1
9/9 [==============================] - 0s 52ms/step - loss: 0.1130 - val_loss: 1.2883
Train on 16 samples, validate on 1 samples
Epoch 1/1
16/16 [==============================] - 0s 26ms/step - loss: 0.2576 - val_loss: 0.5079
Train on 11 samples, validate on 1 samples
Epoch 1/1
11/11 [==============================] - 0s 29ms/step - loss: 0.1102 - val_loss: 0.6795
Train on 9 samples, validate on 1 samples
Epoch 1/1
9/9 [==============================] - 0s 36ms/step - loss: 0.1465 - val_loss: 1.6021
Train on 9 samples, validate on 1 samples
Epoch 1/1
9/9 [==============================] - 0s 28ms/step - loss: 0.2271 - val_loss: 1.4623
Train on 13 samples, validate on 1 samples
Epoch 1/1
13/13 [==============================] - 1s 52ms/step - loss: 0.1418 - val_loss: 1.1146
Train on 9 samples, valid

Train on 9 samples, validate on 1 samples
Epoch 1/1
9/9 [==============================] - 0s 41ms/step - loss: 0.1222 - val_loss: 0.7746
Train on 9 samples, validate on 1 samples
Epoch 1/1
9/9 [==============================] - 0s 26ms/step - loss: 0.0837 - val_loss: 0.6926
Train on 13 samples, validate on 1 samples
Epoch 1/1
13/13 [==============================] - 0s 27ms/step - loss: 0.1402 - val_loss: 0.3444
Train on 15 samples, validate on 1 samples
Epoch 1/1
15/15 [==============================] - 0s 24ms/step - loss: 0.2552 - val_loss: 0.3410
Train on 7 samples, validate on 1 samples
Epoch 1/1
7/7 [==============================] - 1s 73ms/step - loss: 0.1400 - val_loss: 1.0611
Train on 7 samples, validate on 1 samples
Epoch 1/1
7/7 [==============================] - 0s 49ms/step - loss: 0.0652 - val_loss: 0.2283
Train on 10 samples, validate on 1 samples
Epoch 1/1
10/10 [==============================] - 1s 51ms/step - loss: 0.2396 - val_loss: 0.8621
Train on 5 samples, valid

In [18]:
save_name = 'models/no_emb_chorale_' + str(meas_per_seq) + '.h5'
model.save(save_name)

/anaconda3/lib/python3.6/site-packages/keras/engine/topology.py:2368: UserWarning: Layer lstm_2 was passed non-serializable keyword arguments: {'initial_state': [<tf.Tensor 'lstm_1/while/Exit_2:0' shape=(?, 256) dtype=float32>, <tf.Tensor 'lstm_1/while/Exit_3:0' shape=(?, 256) dtype=float32>]}. They will not be included in the serialized model (and thus will be missing at deserialization time).
  str(node.arguments) + '. They will not be included '


### Sampling the notes
- Different sampling methods are used.
    - $\arg\max$: selecting the pitch with highest probability.
        - Deterministic.
        - Potential problem: always choose the most frequent values, the output tends to be repetitive.
    - Temperature sampling with different $\tau$s.
        - Randomly choose based on temperature sampling; stochastic.
        - Higher $\tau$s adds variety to the music generated.
        - Potential problem: large $\tau$ increases the chance of inharmony.
- Sampling methods can be seen at [sampling.py](sampling.py).

In [19]:
# Next: inference mode (sampling).
# Here's the drill:
# 1) encode input and retrieve initial decoder state
# 2) run one step of decoder with this initial state
# and a "start of sequence" token as target.
# Output will be the next target token
# 3) Repeat with the current target token and current states

# Define sampling models
encoder_model = Model(encoder_inputs, encoder_states)

decoder_state_input_h = Input(shape=(latent_dim,))
decoder_state_input_c = Input(shape=(latent_dim,))
decoder_states_inputs = [decoder_state_input_h, decoder_state_input_c]
decoder_outputs, state_h, state_c = decoder_lstm(
    decoder_inputs, initial_state=decoder_states_inputs)
decoder_states = [state_h, state_c]
decoder_outputs = decoder_dense(decoder_outputs)
decoder_model = Model(
    [decoder_inputs] + decoder_states_inputs,
    [decoder_outputs] + decoder_states)

# Reverse-lookup token index to decode sequences back to
# something readable.
reverse_input_char_index = c_idx2val
reverse_target_char_index = c_idx2val
input_token_index = c_val2idx
target_token_index = c_val2idx

In [20]:
import sampling

In [21]:
def decode_sequence(input_seq, samp_fun=sampling.argmax, max_decoder_seq_length=500):
     
    # Encode the input as state vectors.
    states_value = encoder_model.predict(input_seq)

    # Generate empty target sequence of length 1.
    target_seq = np.zeros((1, 1, num_decoder_tokens))
    # Populate the first character of target sequence with the start character.
    target_seq[0, 0, target_token_index['<S>']] = 1.

    # Sampling loop for a batch of sequences
    # (to simplify, here we assume a batch of size 1).
    stop_condition = False
    decoded_sentence = ''
    
    target_ret = []
    target_ret.append(target_seq[0, 0, :])
    
    while not stop_condition:
        output_tokens, h, c = decoder_model.predict(
            [target_seq] + states_value)

        # Sample a token
        sampled_token_index = samp_fun(output_tokens[0, -1, :]) # sampling using argmax
        sampled_char = reverse_target_char_index[sampled_token_index]
        decoded_sentence += str(sampled_char) + ' '

        # Exit condition: either hit max length
        # or find stop character.
        if (sampled_char == '<END>' or
           len(decoded_sentence) > max_decoder_seq_length):
            stop_condition = True

        # Update the target sequence (of length 1).
        target_seq = np.zeros((1, 1, num_decoder_tokens))
        target_seq[0, 0, sampled_token_index] = 1.
        target_ret.append(target_seq[0, 0, :])

        # Update states
        states_value = [h, c]

    return decoded_sentence, np.array([np.array(target_ret)])

In [22]:
def print_seq(input_seq, display_name=True):
    
    naming_func = lambda x: x
    if display_name:
        naming_func = util.get_note_name_by_idx

    sent = ''
    
    for measure in input_seq[0,:,:] :
        indices = np.where(measure > 0)[0]
        if len(indices != 0):
            idx = indices[0]
            sampled_char = reverse_target_char_index[idx]
            if sampled_char == '<S>' or sampled_char == '<END>' or sampled_char == '/': sent += sampled_char
            elif sampled_char >= 0:
                sent += str(naming_func(sampled_char))
            else:
                sent += '-' + str(naming_func(np.abs(sampled_char)))
            sent += ' '
        else: break
    
    return sent

In [23]:
target_token_index = c_val2idx

chords_gen_argmax = []

for seq_index in range(len(encoder_input_data)): # which song
    
    curr_gen = []
    
    filename = 'output/chorale/chords/argmax/' + str(meas_per_seq) + '_' + str(seq_index).zfill(2) + '.txt'
    f = open(filename, 'w')

    input_seq = np.array([encoder_input_data[seq_index][0]]) # input is the first measure
    f.write(print_seq(input_seq, display_name=False) + '\n')
    curr_gen.append(input_seq)
    
    decoded_sentence, target_ret = decode_sequence(input_seq)
    f.write(print_seq(target_ret, display_name=False) + '\n')
    curr_gen.append(target_ret)
    
    for i in range(64):
        input_seq = np.copy(target_ret)
        decoded_sentence, target_ret = decode_sequence(input_seq)
        f.write(print_seq(target_ret, display_name=False) + '\n')
        curr_gen.append(target_ret)

    f.close()
    chords_gen_argmax.append(curr_gen)

In [24]:
chords_gen_tau1 = []

for seq_index in range(len(encoder_input_data)): # which song
    
    curr_gen = []
    
    filename = 'output/chorale/chords/tau1.0/' + str(meas_per_seq) + '_' + str(seq_index).zfill(2) + '.txt'
    f = open(filename, 'w')

    input_seq = np.array([encoder_input_data[seq_index][0]]) # input is the first measure
    f.write(print_seq(input_seq, display_name=False) + '\n')
    curr_gen.append(input_seq)
    
    decoded_sentence, target_ret = decode_sequence(input_seq, samp_fun=sampling.temperature(tau=1.0))
    f.write(print_seq(target_ret, display_name=False) + '\n')
    curr_gen.append(target_ret)
    
    for i in range(64):
        input_seq = np.copy(target_ret)
        decoded_sentence, target_ret = decode_sequence(input_seq, samp_fun=sampling.temperature(tau=1.0))
        f.write(print_seq(target_ret, display_name=False) + '\n')
        curr_gen.append(target_ret)

    f.close()
    chords_gen_tau1.append(curr_gen)

In [25]:
chords_gen_tau2 = []

for seq_index in range(len(encoder_input_data)): # which song
    
    curr_gen = []
    
    filename = 'output/chorale/chords/tau0.9/' + str(meas_per_seq) + '_' + str(seq_index).zfill(2) + '.txt'
    f = open(filename, 'w')

    input_seq = np.array([encoder_input_data[seq_index][0]]) # input is the first measure
    f.write(print_seq(input_seq, display_name=False) + '\n')
    curr_gen.append(input_seq)
    
    decoded_sentence, target_ret = decode_sequence(input_seq, samp_fun=sampling.temperature(tau=0.9))
    f.write(print_seq(target_ret, display_name=False) + '\n')
    curr_gen.append(target_ret)
    
    for i in range(64):
        input_seq = np.copy(target_ret)
        decoded_sentence, target_ret = decode_sequence(input_seq, samp_fun=sampling.temperature(tau=0.9))
        f.write(print_seq(target_ret, display_name=False) + '\n')
        curr_gen.append(target_ret)

    f.close()
    chords_gen_tau2.append(curr_gen)

In [26]:
chords_gen_tau3 = []

for seq_index in range(len(encoder_input_data)): # which song
    
    curr_gen = []
    
    filename = 'output/chorale/chords/tau0.8/' + str(meas_per_seq) + '_' + str(seq_index).zfill(2) + '.txt'
    f = open(filename, 'w')

    input_seq = np.array([encoder_input_data[seq_index][0]]) # input is the first measure
    f.write(print_seq(input_seq, display_name=False) + '\n')
    curr_gen.append(input_seq)
    
    decoded_sentence, target_ret = decode_sequence(input_seq, samp_fun=sampling.temperature(tau=0.8))
    f.write(print_seq(target_ret, display_name=False) + '\n')
    curr_gen.append(target_ret)
    
    for i in range(64):
        input_seq = np.copy(target_ret)
        decoded_sentence, target_ret = decode_sequence(input_seq, samp_fun=sampling.temperature(tau=0.8))
        f.write(print_seq(target_ret, display_name=False) + '\n')
        curr_gen.append(target_ret)

    f.close()
    chords_gen_tau3.append(curr_gen)

## Part 2 - chord sequence to time sequence
### Load data
- _Joplin_ dataset is used. 
- The data is parsed from kern score using <code>rchoraledata</code> tool in [_Humdrum Extras_](http://wiki.ccarh.org/wiki/Humdrum_Extras). See the [embedding notebook](Chord_Embeddings - Joplin.ipynb) for details.
- Filtering data
    - Only songs in 2/4 time signature are selected since most of the songs in this dataset are in 2/4.

In [27]:
encoder_input_data, decoder_input_data, decoder_target_data = util.gen_data_rec_pitch_based_times(c_data, c_val2idx, t_data, t_val2idx, meas_per_seq=meas_per_seq) #[song, measure, chord]

In [28]:
encoder_input_data = util.get_data_fitted(encoder_input_data)
decoder_input_data = util.get_data_fitted(decoder_input_data)
decoder_target_data = util.get_data_fitted(decoder_target_data)

In [29]:
num_encoder_tokens = len(c_val2idx)
num_decoder_tokens = len(t_val2idx)
max_encoder_seq_length = None # different max-seq-len for different songs
max_decoder_seq_length = None

In [30]:
# Define an input sequence and process it.
encoder_inputs = Input(shape=(None, num_encoder_tokens))
encoder = LSTM(latent_dim, return_state=True)
encoder_outputs, state_h, state_c = encoder(encoder_inputs)
# We discard `encoder_outputs` and only keep the states.
encoder_states = [state_h, state_c]

In [31]:
# Set up the decoder, using `encoder_states` as initial state.
decoder_inputs = Input(shape=(None, num_decoder_tokens))
# We set up our decoder to return full output sequences,
# and to return internal states as well. We don't use the
# return states in the training model, but we will use them in inference.
decoder_lstm = LSTM(latent_dim, return_sequences=True, return_state=True)
decoder_outputs, _, _ = decoder_lstm(decoder_inputs,
                                     initial_state=encoder_states)
decoder_dense = Dense(num_decoder_tokens, activation='softmax')
decoder_outputs = decoder_dense(decoder_outputs)

In [32]:
model.reset_states()
model = Model([encoder_inputs, decoder_inputs], decoder_outputs)

In [33]:
model.compile(optimizer='rmsprop', loss='categorical_crossentropy')

In [34]:
model.summary()

__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_5 (InputLayer)            (None, None, 110)    0                                            
__________________________________________________________________________________________________
input_6 (InputLayer)            (None, None, 12)     0                                            
__________________________________________________________________________________________________
lstm_3 (LSTM)                   [(None, 256), (None, 375808      input_5[0][0]                    
__________________________________________________________________________________________________
lstm_4 (LSTM)                   [(None, None, 256),  275456      input_6[0][0]                    
                                                                 lstm_3[0][1]                     
          

In [35]:
batch_size = 64  # Batch size for training.
iterations = 50  # Number of epochs to train for.
latent_dim = 256  # Latent dimensionality of the encoding space.

for it in range(iterations):
    print('='*50)
    print('Iteration {}/{}'.format(it + 1, iterations))
    for i in range(len(c_data)):
        model.fit([encoder_input_data[i], decoder_input_data[i]], decoder_target_data[i],
              batch_size=None,
              epochs=1,
              validation_split=0.01)

Iteration 1/50
Train on 10 samples, validate on 1 samples
Epoch 1/1
10/10 [==============================] - 2s 153ms/step - loss: 1.8286 - val_loss: 1.3768
Train on 7 samples, validate on 1 samples
Epoch 1/1
7/7 [==============================] - 0s 20ms/step - loss: 2.0438 - val_loss: 1.4567
Train on 7 samples, validate on 1 samples
Epoch 1/1
7/7 [==============================] - 0s 16ms/step - loss: 1.7020 - val_loss: 1.4820
Train on 14 samples, validate on 1 samples
Epoch 1/1
14/14 [==============================] - 0s 13ms/step - loss: 0.9442 - val_loss: 0.8389
Train on 5 samples, validate on 1 samples
Epoch 1/1
5/5 [==============================] - 0s 23ms/step - loss: 1.2332 - val_loss: 1.3590
Train on 17 samples, validate on 1 samples
Epoch 1/1
17/17 [==============================] - 0s 10ms/step - loss: 0.6461 - val_loss: 0.6278
Train on 9 samples, validate on 1 samples
Epoch 1/1
9/9 [==============================] - 0s 15ms/step - loss: 0.5896 - val_loss: 1.1312
Train on 

Train on 11 samples, validate on 1 samples
Epoch 1/1
11/11 [==============================] - 0s 15ms/step - loss: 0.7374 - val_loss: 0.3298
Train on 10 samples, validate on 1 samples
Epoch 1/1
10/10 [==============================] - 0s 12ms/step - loss: 0.8467 - val_loss: 0.5762
Train on 6 samples, validate on 1 samples
Epoch 1/1
6/6 [==============================] - 0s 22ms/step - loss: 0.9267 - val_loss: 1.1743
Train on 21 samples, validate on 1 samples
Epoch 1/1
21/21 [==============================] - 0s 11ms/step - loss: 0.5876 - val_loss: 1.0664
Train on 17 samples, validate on 1 samples
Epoch 1/1
17/17 [==============================] - 0s 9ms/step - loss: 0.8223 - val_loss: 0.2884
Train on 10 samples, validate on 1 samples
Epoch 1/1
10/10 [==============================] - 0s 18ms/step - loss: 0.6462 - val_loss: 0.3960
Train on 5 samples, validate on 1 samples
Epoch 1/1
5/5 [==============================] - 0s 22ms/step - loss: 0.8115 - val_loss: 0.6360
Train on 8 samples, 

Train on 7 samples, validate on 1 samples
Epoch 1/1
7/7 [==============================] - 0s 21ms/step - loss: 0.7383 - val_loss: 0.3216
Train on 37 samples, validate on 1 samples
Epoch 1/1
37/37 [==============================] - 1s 14ms/step - loss: 0.9503 - val_loss: 0.7555
Train on 29 samples, validate on 1 samples
Epoch 1/1
29/29 [==============================] - 0s 9ms/step - loss: 0.7234 - val_loss: 0.8604
Train on 11 samples, validate on 1 samples
Epoch 1/1
11/11 [==============================] - 0s 14ms/step - loss: 0.7289 - val_loss: 0.4835
Train on 13 samples, validate on 1 samples
Epoch 1/1
13/13 [==============================] - 0s 12ms/step - loss: 0.6628 - val_loss: 0.3127
Train on 5 samples, validate on 1 samples
Epoch 1/1
5/5 [==============================] - 0s 23ms/step - loss: 0.5461 - val_loss: 0.4632
Train on 18 samples, validate on 1 samples
Epoch 1/1
18/18 [==============================] - 0s 9ms/step - loss: 0.7756 - val_loss: 0.4509
Train on 10 samples, 

Train on 24 samples, validate on 1 samples
Epoch 1/1
24/24 [==============================] - 0s 8ms/step - loss: 0.7014 - val_loss: 1.1975
Train on 6 samples, validate on 1 samples
Epoch 1/1
6/6 [==============================] - 0s 16ms/step - loss: 1.1054 - val_loss: 0.9947
Train on 45 samples, validate on 1 samples
Epoch 1/1
45/45 [==============================] - 0s 10ms/step - loss: 0.9971 - val_loss: 0.4433
Train on 12 samples, validate on 1 samples
Epoch 1/1
12/12 [==============================] - 0s 14ms/step - loss: 0.7799 - val_loss: 0.3810
Train on 12 samples, validate on 1 samples
Epoch 1/1
12/12 [==============================] - 0s 12ms/step - loss: 0.7781 - val_loss: 0.3844
Train on 13 samples, validate on 1 samples
Epoch 1/1
13/13 [==============================] - 0s 12ms/step - loss: 0.6282 - val_loss: 0.7939
Train on 11 samples, validate on 1 samples
Epoch 1/1
11/11 [==============================] - 0s 14ms/step - loss: 0.6130 - val_loss: 0.9431
Train on 8 sample

Train on 13 samples, validate on 1 samples
Epoch 1/1
13/13 [==============================] - 0s 12ms/step - loss: 0.6989 - val_loss: 0.4947
Train on 9 samples, validate on 1 samples
Epoch 1/1
9/9 [==============================] - 0s 14ms/step - loss: 0.5921 - val_loss: 0.6948
Train on 10 samples, validate on 1 samples
Epoch 1/1
10/10 [==============================] - 0s 15ms/step - loss: 0.6433 - val_loss: 0.2503
Train on 9 samples, validate on 1 samples
Epoch 1/1
9/9 [==============================] - 0s 12ms/step - loss: 0.7795 - val_loss: 0.3782
Train on 7 samples, validate on 1 samples
Epoch 1/1
7/7 [==============================] - 0s 17ms/step - loss: 0.6605 - val_loss: 0.7133
Train on 16 samples, validate on 1 samples
Epoch 1/1
16/16 [==============================] - 0s 9ms/step - loss: 0.4514 - val_loss: 0.2539
Train on 11 samples, validate on 1 samples
Epoch 1/1
11/11 [==============================] - 0s 13ms/step - loss: 0.8606 - val_loss: 0.5401
Train on 7 samples, val

...

Train on 11 samples, validate on 1 samples
Epoch 1/1
11/11 [==============================] - 0s 14ms/step - loss: 0.3386 - val_loss: 0.3191
Train on 6 samples, validate on 1 samples
Epoch 1/1
6/6 [==============================] - 0s 16ms/step - loss: 0.7204 - val_loss: 0.7053
Train on 12 samples, validate on 1 samples
Epoch 1/1
12/12 [==============================] - 0s 12ms/step - loss: 0.3347 - val_loss: 1.2295
Train on 5 samples, validate on 1 samples
Epoch 1/1
5/5 [==============================] - 0s 23ms/step - loss: 0.2097 - val_loss: 0.5464
Train on 10 samples, validate on 1 samples
Epoch 1/1
10/10 [==============================] - 0s 16ms/step - loss: 0.2919 - val_loss: 0.4278
Train on 5 samples, validate on 1 samples
Epoch 1/1
5/5 [==============================] - 0s 23ms/step - loss: 0.1003 - val_loss: 0.7574
Train on 9 samples, validate on 1 samples
Epoch 1/1
9/9 [==============================] - 0s 12ms/step - loss: 0.2188 - val_loss: 0.5566
Train on 7 samples, valid

Train on 8 samples, validate on 1 samples
Epoch 1/1
8/8 [==============================] - 0s 15ms/step - loss: 0.1296 - val_loss: 0.3788
Train on 13 samples, validate on 1 samples
Epoch 1/1
13/13 [==============================] - 0s 9ms/step - loss: 0.2951 - val_loss: 0.5430
Train on 18 samples, validate on 1 samples
Epoch 1/1
18/18 [==============================] - 0s 8ms/step - loss: 0.2903 - val_loss: 1.4146
Train on 9 samples, validate on 1 samples
Epoch 1/1
9/9 [==============================] - 0s 10ms/step - loss: 0.2639 - val_loss: 0.2618
Train on 9 samples, validate on 1 samples
Epoch 1/1
9/9 [==============================] - 0s 12ms/step - loss: 0.2156 - val_loss: 0.5918
Train on 8 samples, validate on 1 samples
Epoch 1/1
8/8 [==============================] - 0s 17ms/step - loss: 0.1156 - val_loss: 0.4883
Train on 6 samples, validate on 1 samples
Epoch 1/1
6/6 [==============================] - 0s 15ms/step - loss: 0.1183 - val_loss: 0.2545
Train on 14 samples, validate 

Train on 9 samples, validate on 1 samples
Epoch 1/1
9/9 [==============================] - 0s 13ms/step - loss: 0.1115 - val_loss: 0.3708
Train on 11 samples, validate on 1 samples
Epoch 1/1
11/11 [==============================] - 0s 14ms/step - loss: 0.1166 - val_loss: 0.5399
Train on 8 samples, validate on 1 samples
Epoch 1/1
8/8 [==============================] - 0s 16ms/step - loss: 0.1343 - val_loss: 0.3760
Train on 6 samples, validate on 1 samples
Epoch 1/1
6/6 [==============================] - 0s 19ms/step - loss: 0.1334 - val_loss: 0.2495
Train on 7 samples, validate on 1 samples
Epoch 1/1
7/7 [==============================] - 0s 20ms/step - loss: 0.0822 - val_loss: 0.3933
Train on 14 samples, validate on 1 samples
Epoch 1/1
14/14 [==============================] - 0s 11ms/step - loss: 0.1558 - val_loss: 0.5978
Train on 5 samples, validate on 1 samples
Epoch 1/1
5/5 [==============================] - 0s 24ms/step - loss: 0.0895 - val_loss: 0.1738
Train on 8 samples, validate

Train on 10 samples, validate on 1 samples
Epoch 1/1
10/10 [==============================] - 0s 18ms/step - loss: 0.1476 - val_loss: 0.7586
Train on 5 samples, validate on 1 samples
Epoch 1/1
5/5 [==============================] - 0s 27ms/step - loss: 0.1679 - val_loss: 0.3087
Train on 7 samples, validate on 1 samples
Epoch 1/1
7/7 [==============================] - 0s 17ms/step - loss: 0.0867 - val_loss: 0.5532
Train on 7 samples, validate on 1 samples
Epoch 1/1
7/7 [==============================] - 0s 19ms/step - loss: 0.1677 - val_loss: 0.4987
Train on 8 samples, validate on 1 samples
Epoch 1/1
8/8 [==============================] - 0s 15ms/step - loss: 0.2133 - val_loss: 0.4332
Train on 7 samples, validate on 1 samples
Epoch 1/1
7/7 [==============================] - 0s 17ms/step - loss: 0.0956 - val_loss: 0.4374
Train on 14 samples, validate on 1 samples
Epoch 1/1
14/14 [==============================] - 0s 10ms/step - loss: 0.1304 - val_loss: 0.7972
Train on 10 samples, validat

Train on 9 samples, validate on 1 samples
Epoch 1/1
9/9 [==============================] - 0s 14ms/step - loss: 0.1098 - val_loss: 0.4017
Train on 13 samples, validate on 1 samples
Epoch 1/1
13/13 [==============================] - 0s 11ms/step - loss: 0.0885 - val_loss: 0.6881
Train on 7 samples, validate on 1 samples
Epoch 1/1
7/7 [==============================] - 0s 18ms/step - loss: 0.0391 - val_loss: 0.8318
Train on 9 samples, validate on 1 samples
Epoch 1/1
9/9 [==============================] - 0s 13ms/step - loss: 0.1107 - val_loss: 0.8795
Train on 9 samples, validate on 1 samples
Epoch 1/1
9/9 [==============================] - 0s 13ms/step - loss: 0.1639 - val_loss: 1.8382
Train on 9 samples, validate on 1 samples
Epoch 1/1
9/9 [==============================] - 0s 13ms/step - loss: 0.1315 - val_loss: 0.4554
Train on 10 samples, validate on 1 samples
Epoch 1/1
10/10 [==============================] - 0s 21ms/step - loss: 0.1088 - val_loss: 0.8280
Train on 14 samples, validat

In [36]:
save_name = 'models/no_emb_chorale_times' + str(meas_per_seq) + '.h5'
model.save(save_name)

/anaconda3/lib/python3.6/site-packages/keras/engine/topology.py:2368: UserWarning: Layer lstm_4 was passed non-serializable keyword arguments: {'initial_state': [<tf.Tensor 'lstm_3/while/Exit_2:0' shape=(?, 256) dtype=float32>, <tf.Tensor 'lstm_3/while/Exit_3:0' shape=(?, 256) dtype=float32>]}. They will not be included in the serialized model (and thus will be missing at deserialization time).
  str(node.arguments) + '. They will not be included '


In [58]:
# Next: inference mode (sampling).
# Here's the drill:
# 1) encode input and retrieve initial decoder state
# 2) run one step of decoder with this initial state
# and a "start of sequence" token as target.
# Output will be the next target token
# 3) Repeat with the current target token and current states

# Define sampling models
encoder_model = Model(encoder_inputs, encoder_states)

decoder_state_input_h = Input(shape=(latent_dim,))
decoder_state_input_c = Input(shape=(latent_dim,))
decoder_states_inputs = [decoder_state_input_h, decoder_state_input_c]
decoder_outputs, state_h, state_c = decoder_lstm(
    decoder_inputs, initial_state=decoder_states_inputs)
decoder_states = [state_h, state_c]
decoder_outputs = decoder_dense(decoder_outputs)
decoder_model = Model(
    [decoder_inputs] + decoder_states_inputs,
    [decoder_outputs] + decoder_states)

# Reverse-lookup token index to decode sequences back to
# something readable.
reverse_input_char_index = c_idx2val
reverse_target_char_index = t_idx2val
input_token_index = c_val2idx
target_token_index = t_val2idx

In [68]:
def decode_sequence(input_seq, samp_fun=sampling.argmax, max_decoder_seq_length=500):
     
    # Encode the input as state vectors.
    states_value = encoder_model.predict(input_seq)

    # Generate empty target sequence of length 1.
    target_seq = np.zeros((1, 1, num_decoder_tokens))
    # Populate the first character of target sequence with the start character.
    target_seq[0, 0, target_token_index['<S>']] = 1.

    # Sampling loop for a batch of sequences
    # (to simplify, here we assume a batch of size 1).
    stop_condition = False
    decoded_sentence = ''
    
    target_ret = []
    target_ret.append(target_seq[0, 0, :])
    
    while not stop_condition:
        output_tokens, h, c = decoder_model.predict(
            [target_seq] + states_value)

        # Sample a token
        sampled_token_index = samp_fun(output_tokens[0, -1, :]) # sampling using argmax

        sampled_char = reverse_target_char_index[sampled_token_index]
        decoded_sentence += str(sampled_char) + ' '

        # Exit condition: either hit max length
        # or find stop character.
        if (sampled_char == '<END>' or
           len(decoded_sentence) > max_decoder_seq_length):
            stop_condition = True

        # Update the target sequence (of length 1).
        target_seq = np.zeros((1, 1, num_decoder_tokens))
        target_seq[0, 0, sampled_token_index] = 1.
        target_ret.append(target_seq[0, 0, :])

        # Update states
        states_value = [h, c]

    return decoded_sentence, np.array([np.array(target_ret)])

In [69]:
target_token_index = t_val2idx
# generate from argmax chords
for i, song in enumerate(chords_gen_argmax): # which song
    
    filename = 'output/chorale/times/argmax/' + str(meas_per_seq) + '_' + str(i).zfill(2) + '.txt'
    f = open(filename, 'w')

    for seq in song:
        input_seq = np.array(seq) # input is the first measure
        decoded_sentence, target_ret = decode_sequence(input_seq)
        f.write(print_seq(target_ret, display_name=False) + '\n')

    f.close()

In [70]:
reverse_target_char_index = t_idx2val
# generate from tau1.0 chords
for i, song in enumerate(chords_gen_tau1): # which song
    
    filename = 'output/chorale/times/tau1.0/' + str(meas_per_seq) + '_' + str(i).zfill(2) + '.txt'
    f = open(filename, 'w')

    for seq in song:
        input_seq = np.array(seq) # input is the first measure
        decoded_sentence, target_ret = decode_sequence(input_seq)
        f.write(print_seq(target_ret, display_name=False) + '\n')

    f.close()

In [71]:
# generate from tau0.9 chords
for i, song in enumerate(chords_gen_tau2): # which song
    
    filename = 'output/chorale/times/tau0.9/' + str(meas_per_seq) + '_' + str(i).zfill(2) + '.txt'
    f = open(filename, 'w')

    for seq in song:
        input_seq = np.array(seq) # input is the first measure
        decoded_sentence, target_ret = decode_sequence(input_seq)
        f.write(print_seq(target_ret, display_name=False) + '\n')

    f.close()

In [72]:
# generate from tau0.8 chords
for i, song in enumerate(chords_gen_tau3): # which song
    
    filename = 'output/chorale/times/tau0.8/' + str(meas_per_seq) + '_' + str(i).zfill(2) + '.txt'
    f = open(filename, 'w')

    for seq in song:
        input_seq = np.array(seq) # input is the first measure
        decoded_sentence, target_ret = decode_sequence(input_seq)
        f.write(print_seq(target_ret, display_name=False) + '\n')

    f.close()